In [10]:
# Install dependencies
!pip install -q transformers accelerate bert-score

# Import required libraries
import os
import pandas as pd
import torch
from PIL import Image
from tqdm import tqdm
import re
from sklearn.metrics import classification_report
from bert_score import score as bertscore
from transformers import Blip2Processor, Blip2ForConditionalGeneration


   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 61.1/61.1 kB 2.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 363.4/363.4 MB 4.7 MB/s eta 0:00:000:00:0100:01
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 664.8/664.8 MB 2.4 MB/s eta 0:00:000:00:0100:01
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 211.5/211.5 MB 2.7 MB/s eta 0:00:000:00:0100:01
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 56.3/56.3 MB 5.3 MB/s eta 0:00:000:00:0100:01
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 127.9/127.9 MB 13.5 MB/s eta 0:00:00:00:0100:01
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 207.5/207.5 MB 8.2 MB/s eta 0:00:000:00:0100:01
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 21.1/21.1 MB 82.3 MB/s eta 0:00:00:00:0100:01


2025-05-14 04:19:42.788367: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:477] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
E0000 00:00:1747196383.004370      35 cuda_dnn.cc:8310] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
E0000 00:00:1747196383.069794      35 cuda_blas.cc:1418] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered


In [11]:
import kagglehub

# Download latest version of your dataset
dataset_path = kagglehub.dataset_download("naval2024099/vqa-vr")

print("📁 Dataset downloaded to:", dataset_path)


📁 Dataset downloaded to: /kaggle/input/vqa-vr


In [ ]:
# Load BLIP-2 model and processor
device = "cuda" if torch.cuda.is_available() else "cpu"

processor = Blip2Processor.from_pretrained("Salesforce/blip2-opt-2.7b")
model = Blip2ForConditionalGeneration.from_pretrained(
    "Salesforce/blip2-opt-2.7b",
    device_map="auto",
    torch_dtype=torch.float16
)

model.eval()
print("🚀 Model loaded on:", device)


Using a slow image processor as `use_fast` is unset and a slow processor was saved with this model. `use_fast=True` will be the default behavior in v4.52, even if the model was saved with a slow processor. This will result in minor differences in outputs. You'll still be able to use a slow processor with `use_fast=False`.


preprocessor_config.json:   0%|          | 0.00/432 [00:00<?, ?B/s]

tokenizer_config.json:   0%|          | 0.00/882 [00:00<?, ?B/s]

vocab.json:   0%|          | 0.00/798k [00:00<?, ?B/s]

merges.txt:   0%|          | 0.00/456k [00:00<?, ?B/s]

...

model-00002-of-00002.safetensors:   0%|          | 0.00/4.98G [00:00<?, ?B/s]

model-00001-of-00002.safetensors:   0%|          | 0.00/10.0G [00:00<?, ?B/s]

Loading checkpoint shards:   0%|          | 0/2 [00:00<?, ?it/s]

generation_config.json:   0%|          | 0.00/141 [00:00<?, ?B/s]

🚀 Model loaded on: cuda


In [13]:
# Adjust this path if needed
csv_path = os.path.join(dataset_path, "test_main_image_id.csv")
df = pd.read_csv(csv_path)
print(f"✅ Loaded {len(df)} samples from CSV.")


✅ Loaded 106670 samples from CSV.


In [14]:
def normalize(text):
    if not isinstance(text, str):
        return ""
    return re.sub(r"[^\w\s]", "", text.lower().strip())


In [ ]:
predictions = []

# Use a small subset for testing (optional)
small_test = df[:100]
IMAGE_ROOT = "/kaggle/input/vqa-vr/filtered_images_corrected"

for _, row in tqdm(df.iterrows(), total=len(df)):
    question = normalize(row["question"])
    correct_answer = normalize(row["correct_answer"])
    rel_path = row["path"]
    image_path = os.path.join(IMAGE_ROOT, rel_path)

    # Prompt design
    prompt = f"{question} answer:"
    
    try:
        image = Image.open(image_path).convert("RGB")
    except Exception as e:
        predictions.append("error")
        continue

    # Model inference
    inputs = processor(images=image, text=prompt, return_tensors="pt").to(device, torch.float16 if torch.cuda.is_available() else torch.float32)
    output = model.generate(**inputs, max_new_tokens=10)
    pred = processor.decode(output[0], skip_special_tokens=True).strip()

    # Postprocess prediction
    if pred.lower().startswith(prompt.lower()):
        pred = pred[len(prompt):].strip()
    
    # Safe normalization
    if pred:
        first_word = pred.split(",")[0].split()[0]
        pred = normalize(first_word)
    else:
        pred = "unknown"
    
    predictions.append(pred)

  0%|          | 3/106670 [00:02<18:43:38,  1.58it/s]The `language_model` is not in the `hf_device_map` dictionary and you are running your script in a multi-GPU environment. this may lead to unexpected behavior when using `accelerate`. Please pass a `device_map` that contains `language_model` to remove this warning. Please refer to https://github.com/huggingface/blog/blob/main/accelerate-large-models.md for more details on creating a `device_map` for large models.
The `language_model` is not in the `hf_device_map` dictionary and you are running your script in a multi-GPU environment. this may lead to unexpected behavior when using `accelerate`. Please pass a `device_map` that contains `language_model` to remove this warning. Please refer to https://github.com/huggingface/blog/blob/main/accelerate-large-models.md for more details on creating a `device_map` for large models.
  0%|          | 5/106670 [00:02<9:47:07,  3.03it/s] The `language_model` is not in the `hf_device_map` dictionar

In [22]:
# Add predictions
df = df.reset_index(drop=True)
df["predicted_answer"] = predictions

In [26]:
from sklearn.metrics import accuracy_score, f1_score, classification_report



# Normalize for evaluation
y_true = [normalize(a) for a in df["correct_answer"]]
y_pred = [normalize(a) for a in df["predicted_answer"]]

# Accuracy
exact_matches = [1 if p == r else 0 for p, r in zip(y_pred, y_true)]
accuracy = sum(exact_matches) / len(exact_matches)

# F1 Score
f1 = f1_score(y_true, y_pred, average='macro', zero_division=0)

# BERTScore
P, R, F1_bert = bertscore(y_pred, y_true, lang="en", verbose=True)

# Report
print(f"\n✅ Accuracy: {accuracy:.4f}")
print(f"🎯 F1 Score (macro): {f1:.4f}")
print(f"📊 BERTScore F1: {F1_bert.mean():.4f}")
print("\n📋 Classification Report:")
print(classification_report(y_true, y_pred, zero_division=0))


tokenizer_config.json:   0%|          | 0.00/25.0 [00:00<?, ?B/s]

config.json:   0%|          | 0.00/482 [00:00<?, ?B/s]

vocab.json:   0%|          | 0.00/899k [00:00<?, ?B/s]

merges.txt:   0%|          | 0.00/456k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/1.36M [00:00<?, ?B/s]

...

calculating scores...
computing bert embedding.


  0%|          | 0/84 [00:00<?, ?it/s]

computing greedy matching.


  0%|          | 0/1667 [00:00<?, ?it/s]

done in 22.08 seconds, 4830.83 sentences/sec

✅ Accuracy: 0.1853
🎯 F1 Score (macro): 0.0270
📊 BERTScore F1: 0.9411

📋 Classification Report:
                                                                                                                                                                     precision    recall  f1-score   support

                                                                                                                                                                          0.00      0.00      0.00       336
                                                                                                                                                                  0       0.00      0.00      0.00         0
                                                                                                                                                                  1       0.00      0.00      0.00         2
                                      

In [25]:
# Save predictions to CSV
df.to_csv("blip2_vqa_predictions.csv", index=False)
print("🔽 Predictions saved to blip2_vqa_predictions.csv")


🔽 Predictions saved to blip2_vqa_predictions.csv
